# Intro

> **Onur Ümit Şener** <br> 
> **2006102010**

[Original Source](https://www.planecrashinfo.com/database.htm) of the _"Airplane Crash Data Since 1908"_ dataset from _[Kaggle](https://www.kaggle.com/datasets/cgurkan/airplane-crash-data-since-1908)_


## About Dataset

`copied from Kaggle`


### Context

The aviation accident database throughout the world, from 1908-2019.

- All civil and commercial aviation accidents of scheduled and non-scheduled passenger airliners worldwide, which resulted in a fatality (including all U.S. Part 121 and Part 135 fatal accidents)
- All cargo, positioning, ferry and test flight fatal accidents.
- All military transport accidents with 10 or more fatalities.
- All commercial and military helicopter accidents with greater than 10 fatalities.
- All civil and military airship accidents involving fatalities.
- Aviation accidents involving the death of famous people.
- Aviation accidents or incidents of noteworthy interest.


### Content

Data is scraped from planecrashinfo.com. Below you can find the dataset column descriptions:

- Date: Date of accident, in the format - January 01, 2001
- Time: Local time, in 24 hr. format unless otherwise specified
- Airline/Op: Airline or operator of the aircraft
- Flight #: Flight number assigned by the aircraft operator
- Route: Complete or partial route flown prior to the accident
- AC Type: Aircraft type
- Reg: ICAO registration of the aircraft
- cn / ln: Construction or serial number / Line or fuselage number
- Aboard: Total aboard (passengers / crew)
- Fatalities: Total fatalities aboard (passengers / crew)
- Ground: Total killed on the ground
- Summary: Brief description of the accident and cause if known


## Questions
> 1. What is the corrolation between the fleet size and crash rates?
> 2. Which areas are more prone to crashes? 
> 3. What type of aircraft are involved in crashes the most?
> 4. What scope of years did the most aircraft crashes occur?

# Code

## Imports

In [1]:
import json
from datetime import datetime
from pprint import pprint

import folium
import geopandas as gpd
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
import seaborn as sns
from folium.plugins import HeatMap
from fuzzywuzzy import fuzz, process
from plotly.subplots import make_subplots

### Defaults

In [2]:
pio.templates.default = 'plotly_dark'

## Data Cleaning

### Wind Data
[Source](http://iridl.ldeo.columbia.edu/ds:/SOURCES/.NOAA/.NCEP-NCAR/.CDAS-1/.mc9120/.Intrinsic/.PressureLevel/.u/decompress/dup/mul/SOURCES/.NOAA/.NCEP-NCAR/.CDAS-1/.mc9120/.Intrinsic/.PressureLevel/.v/decompress/dup/mul/add/sqrt//long_name/%28speed%5Bm/s%5D%29def/windspeed_anomaly_colors/DATA/0/3/6/9/12/15/18/21/24/27/30/VALUES//name/%28speed%29def/SOURCES/.NOAA/.NCEP-NCAR/.CDAS-1/.mc9120/.Intrinsic/.PressureLevel/.u//name/%28u%29def/SOURCES/.NOAA/.NCEP-NCAR/.CDAS-1/.mc9120/.Intrinsic/.PressureLevel/.v//name/%28v%29def/:ds/speed/+/speed/ngridtable/5+ncoltable.html)

[Useful](https://globalwindatlas.info/en/download/gis-files)


In [3]:
# wind = pd.read_csv('global wind data.csv')
wind = pd.read_csv('https://drive.google.com/uc?export=download&id=1c4jmnDBJO6vD3J8XptEbGMPqCFxpVWzd')
wind.rename(columns={'speed[m/s]': 'Speed'}, inplace=True)
wind['Longitude'] -= 180
WIND_INTERVAL = 10512
wind.sample(10)

Longitude  Latitude  Pressure     Time      Speed
2028903       37.5      90.0     400.0  1960-12   1.983036
1124643     -172.5     -90.0     600.0  1960-07   6.320337
288226        25.0      15.0     150.0  1960-02  19.499790
831570       105.0      72.5     100.0  1960-05   0.344050
1270555      -72.5     -67.5     925.0  1960-08  11.995290
1628707      -12.5     -80.0     925.0  1960-10   8.208507
1322464      100.0     -55.0     400.0  1960-08  17.469310
409750        -5.0     -87.5     600.0  1960-03   6.205840
1331196      -30.0     -25.0     300.0  1960-08  41.578560
781775       177.5      25.0     400.0  1960-05  14.765030

### Crash Data

In [4]:
raw_data = pd.read_csv('Airplane_Crashes_and_Fatalities.csv')
print(raw_data.shape)
raw_data.sample(10)

(4967, 17)


Date   Time                     Location  \
134   10/30/1927    NaN    New Brunswick, New Jersey   
1092  01/30/1949  16:22    Port Washington, New York   
3076  08/19/1980  19:08         Riyadh, Saudi Arabia   
3280  09/21/1984    NaN  Near Sarakchar, Afghanistan   
2925  12/02/1977    NaN       Near Al Bayda, Lebanon   
3682  05/13/1991  13:19        Grand Canyon, Airzona   
3722  11/20/1991  18:14            Davis, California   
4701  03/22/2009  14:28               Butte, Montana   
4843  03/08/2013  08:15      Near Dillingham, Alaska   
4953  07/10/2018  07:44       Pretoria, South Africa   

                               Operator Flight #  \
134              Colonial Air Transport      NaN   
1092         Pan American World Airways      100   
3076             Saudi Arabian Airlines      163   
3280       Military - Russian Air Force      NaN   
2925          Balkan Bulgarian Airlines      NaN   
3682   Air Taxi - Air Grand Canyon Inc.      NaN   
3722  Air Taxi - Airis Helicopters Inc.      NaN   
4701                  Eagle Cap Leasing      NaN   
4843                      Ace Air Cargo       51   
4953                          Rovos Air      NaN   

                                   Route                      AC Type  \
134                                  NaN               Fairchild FC-2   
1092                                 NaN  Lockheed L-749 / Cessna 140   
3076                     Riyadh - Jeddah    Lockheed 1011-200 TriStar   
3280                                 NaN                Antonov AN-12   
2925                   Jeddah - Benghazi              Tupolev TU-154B   
3682                   Local sightseeing                  Cessna 207A   
3722  San Francisco, CA - Sacramento, CA                    Bell 206B   
4701            Oroville, CA - Butte, MT             Pilatus PC-12/45   
4843            King Salmon - Dillingham             Beechcraft 1900C   
4953                         Test Flight               Convair CV-340   

         Registration     cn/ln  Aboard  Aboard Passangers  Aboard Crew  \
134               NaN        20     4.0                3.0          1.0   
1092  NC86530/NC76981   2528 /?    35.0               23.0         12.0   
3076           HZ-AHK      1169   301.0              287.0         14.0   
3280              NaN       NaN    50.0               45.0          5.0   
2925           LZ-BTN        54   165.0              159.0          6.0   
3682           N6280H  20700463     7.0                6.0          1.0   
3722           N5011K      2580     3.0                2.0          1.0   
4701           N128CM       403    14.0               13.0          1.0   
4843           N116AX     UC-17     2.0                0.0          2.0   
4953           ZS-BRV       215    19.0               16.0          3.0   

      Fatalities  Fatalities Passangers  Fatalities Crew  Ground  \
134          4.0                    3.0              1.0     0.0   
1092         2.0                    1.0              1.0     0.0   
3076       301.0                  287.0             14.0     0.0   
3280        50.0                   45.0              5.0     0.0   
2925        59.0                   59.0              0.0     0.0   
3682         7.0                    6.0              1.0     0.0   
3722         3.0                    2.0              1.0     0.0   
4701        14.0                   13.0              1.0     0.0   
4843         2.0                    0.0              2.0     0.0   
4953         1.0                    0.0              1.0     1.0   

                                                Summary  
134   Went into a tailspin and crashed into a corn f...  
1092  Midair collision. Two killed on the Cessna, no...  
3076  The flight experienced a fire in the aft cargo...  
3280                        Shot down by Afghan rebels.  
2925  After not being able to land at the scheduled ...  
3682  The airplane crashed into a wooded area about ...  
3722  The helicopter impacted the gro

#### data init

In [5]:
data = raw_data.copy()
data.rename(columns={'AC Type': 'ACFT Type'}, inplace=True)

In [6]:
date_time_list = []
for idx in range(data.shape[0]-1):
    date = data['Date'].iloc[idx]
    time = data['Time'].iloc[idx]
    time_null =  '12:00'

    date_time = f'{date} {time}' if not pd.isna(time) else f'{date} {time_null}'
    try:
        date_time_obj = datetime.strptime(date_time, '%m/%d/%Y %H:%M')
    except:
        date_time_obj = None
    date_time_list.append(date_time_obj)
date_time_df = pd.DataFrame(date_time_list)

In [7]:
data.insert(3, 'datetime', date_time_df)
data.sample(5, random_state=55)

Date   Time              Location            datetime  \
1946  04/19/1962    NaN        Near Hong Kong 1962-04-19 12:00:00   
2418  09/20/1969  16:00  Near Hoi An, Vietnam 1969-09-20 16:00:00   
1780  09/29/1959  23:09        Buffalo, Texas 1959-09-29 23:09:00   
337   04/10/1934    NaN     Ningpo Bay, China 1934-04-10 12:00:00   
3681  05/09/1991  02:37   Sulawesi, Indonesia 1991-05-09 02:37:00   

                                 Operator Flight #                     Route  \
1946            Military - U.S. Air Force      NaN       Hong Kong - Formosa   
2418          Air Vietnam (South Vietnam)      NaN          Pleiku - Da Nang   
1780                     Braniff Airlines      542          Houston - Dallas   
337   China National Aviation Corporation      NaN                       NaN   
3681           Merpati Nusantara Airlines     7533  Ambon - Ternate - Manado   

                       ACFT Type Registration  cn/ln  Aboard  \
1946                Douglas C-47          NaN    NaN    16.0   
2418    Douglas DC-4 / USAF F-4E       XV-NUG  10860    76.0   
1780       Lockheed 188A Electra       N9705C   1090    34.0   
337              Sikorsky S-38BB        NV17V    NaN     3.0   
3681  Fokker F-27 Friendship 600       PK-MFD  10399    13.0   

      Aboard Passangers  Aboard Crew  Fatalities  Fatalities Passangers  \
1946               10.0          6.0        15.0                   10.0   
2418               71.0          5.0        74.0                   69.0   
1780               28.0          6.0        34.0                   28.0   
337                 1.0          2.0         3.0                    1.0   
3681                8.0          5.0        13.0                    8.0   

      Fatalities Crew  Ground  \
1946              5.0     0.0   
2418              5.0     2.0   
1780              6.0     0.0   
337               2.0     0.0   
3681              5.0     0.0   

                                                Summary  
1946  Crashed into a fog-shrouded mountain minutes a...  
2418  Midair collision. The F-4E landed safely. The ...  
1780  In-flight separation of the left wing resulted...  
337                                                 NaN  
3681  Crashed into Mt. Klabat in heavy fog while des...

#### clean_data init

In [8]:
numeric_data = data[[
    'Aboard',
    'Aboard Passangers',
    'Aboard Crew',
    'Fatalities',
    'Fatalities Passangers',
    'Fatalities Crew',
    'Ground'
    ]]

In [9]:
clean_data = data.copy()

dropped_columns = [
    'Aboard Passangers',
    'Aboard Crew',
    'Fatalities Passangers',
    'Fatalities Crew',
    'Summary'
]

clean_data.drop(dropped_columns, axis=1, inplace=True);

In [10]:
print(
    clean_data['Location'].isna().any(),
    clean_data[clean_data['Location'].isna()].index.values,
    sep='\n'
)

True
[ 360  643  995 2878]


In [11]:
clean_data.drop(clean_data[clean_data['Location'].isna()].index.values, inplace=True)
clean_data.reset_index(drop=True, inplace=True)
clean_data.sample(10, random_state=5)

Date   Time                             Location  \
2315  04/08/1968  15:35    Heathrow Airport, London, England   
901   11/05/1946  18:30                  Near Moscow, Russia   
2256  04/02/1967    NaN                       Off Lima, Peru   
2529  07/03/1971  18:10                      Hokkaido, Japan   
4865  04/19/2014  19:45                 Ramos Arizpe, Mexico   
4388  09/14/2002    NaN      Paranapanema, Sao Paulo, Brazil   
2663  05/29/1973    NaN  Near Rimouski, Prov. Quebec, Canada   
3234  11/27/1983  10:06                Madrid-Barajas, Spain   
710   04/06/1944  15:48                    Near Nome, Alaska   
1734  01/16/1959  21:40         Off Mar del Plata, Argentina   

                datetime                          Operator Flight #  \
2315 1968-04-08 15:35:00          British Overseas Airways      712   
901  1946-11-05 18:30:00                          Aeroflot      NaN   
2256 1967-04-02 12:00:00                Caribbean Airlines      NaN   
2529 1971-07-03 18:10:00      Toa Domestic Airline (Japan)       63   
4865 2014-04-19 19:45:00         Lineas Aereas Comerciales      NaN   
4388 2002-09-14 12:00:00                  Total  Air Lines      NaN   
2663 1973-05-29 12:00:00                         Air Gaspé      NaN   
3234 1983-11-27 10:06:00                           AVIANCA       11   
710  1944-04-06 15:48:00        Pan American World Airways      NaN   
1734 1959-01-16 21:40:00  Austral Lineas Aeras (Argentina)      205   

                             Route                              ACFT Type  \
2315               London - Zurich                       Boeing B-707-465   
901          Riga, Latvia - Moscow                           Douglas C-47   
2256       Miami - Lima - Asunción                   Lockheed 18 Lodestar   
2529            Sapporo - Hakodate                        NAMC YS-11A-227   
4865        Cozumel - Ramos Arizpe  British Aerospace BAe 125-700A Hawker   
4388          Guarulhos - Londrina                             ATR 42-300   
2663                           NaN                           Douglas DC-3   
3234       Paris - Madrid - Bogota                      Boeing B-747-283B   
710               Nome - Fairbanks                           Pilgrim 100B   
1734  Buenos Aires - Mar del Plata                    Curtiss C-46A-50-CU   

     Registration  cn/ln  Aboard  Fatalities  Ground  
2315       G-ARWE  18373   127.0         5.0     0.0  
901     SSSR-L946    NaN    26.0        13.0     NaN  
2256        N706G   2625     5.0         5.0     0.0  
2529       JA8764   2134    68.0        68.0     0.0  
4865       XA-UKR  25719     8.0         8.0     0.0  
4388       PT-MTS     26     2.0         2.0     0.0  
2663       CF-QBB  10081     4.0         4.0     0.0  
3234      HK-2910  21381   192.0       181.0     0.0  
710        NC742N    NaN     6.0         6.0     0.0  
1734       LV-GED  30514    52.0        51.0     0.0

In [12]:
for col in clean_data.columns:
    print(col)

Date
Time
Location
datetime
Operator
Flight #
Route
ACFT Type
Registration
cn/ln
Aboard
Fatalities
Ground


In [13]:
unique_cols = [
    'Location',
    'Operator',
    'Route',
    'ACFT Type'
]

#### unique_dict init

In [14]:
unique_dict = {}
for col in unique_cols:   
    unique_df = pd.DataFrame()
    
    unique_values = clean_data[col].value_counts().to_dict()
    unique_df['Name'] = unique_values.keys()
    unique_df['Number'] = unique_values.values()
    
    unique_dict[col] = unique_df
unique_dict

{'Location':                      Name  Number
 0          Moscow, Russia      17
 1     Manila, Philippines      14
 2      New York, New York      14
 3            Cairo, Egypt      13
 4       Sao Paulo, Brazil      13
 ...                   ...     ...
 4096   Mount Oyama, Japan       1
 4097        Triel, France       1
 4098    Near Lazo, Russia       1
 4099       Payette, Idaho       1
 4100    Rawalpindi, India       1
 
 [4101 rows x 2 columns],
 'Operator':                                          Name  Number
 0                                    Aeroflot     254
 1                   Military - U.S. Air Force     140
 2                                  Air France      72
 3                          Deutsche Lufthansa      62
 4                            United Air Lines      44
 ...                                       ...     ...
 2236                   Houston Metro Airlines       1
 2237                      Wenela Air Services       1
 2238                  Sierra Pac

#### Approximate String Matching **[Do NOT run it literally took 25 minutes]**
I suffered so much doing this.<br>It took more than a day to complete this

In [15]:
# clean_unique_dict = {}
# for key in unique_dict:
#     drop_list = []
#     df = unique_dict[key].copy()

#     for subkey in (df['Name']):
#         extraction = process.extract(subkey, df['Name'])

#         for e in extraction[1:-1]:
#             idx = df.loc[df['Name'] == subkey].index[0]
#             key_value = df.at[idx, 'Number']
#             found_value = df.at[e[2], 'Number']

#             if e[1] >= 90:
#                 key_value += found_value
#                 drop_list.append(df.loc[df['Name'] == e[0]].index[0])

#     df = df.drop(drop_list)
#     df.reset_index(drop=True, inplace=True)
#     clean_unique_dict[key] = df

# clean_unique_dict

In [16]:
# for x in clean_unique_dict:
#     j = clean_unique_dict[x].to_json()
#     clean_unique_dict[x] = j

In [17]:
# unique_json = json.dumps(clean_unique_dict)
# with open('unique_dict.json', 'w') as f:
#     f.write(unique_json)

##### Uniques Read from File 

In [18]:
with open('unique_dict.json', 'r') as f:
    clean_unique_dict = eval(f.read())
for x in clean_unique_dict:
    d = json.loads(clean_unique_dict[x])
    clean_unique_dict[x] = pd.DataFrame.from_dict(d)

#### Geocoding **[Do NOT run this takes even longer** (35 minutes)**]**

In [19]:
# crash_locations = gpd.tools.geocode(
#     clean_unique_dict['Location']['Name'],
#     provider='nominatim",
#     user_agent="kaggle_learn",
#     #user_agent="autogis2022",
#     timeout=10
# )
# crash_locations.head()

In [20]:
# crash_locations.to_csv('crash_locations1.csv', encoding='utf-8-sig')

##### Geocoding Read from File 

In [21]:
crash_locations = pd.read_csv('crash_locations1.csv')

In [22]:
clean_crash_locations = pd.read_csv('crash_locations.csv')
clean_crash_locations['Number of Crashes'] = unique_dict['Location']['Number']
clean_crash_locations.dropna(inplace=True)
clean_crash_locations.reset_index(drop=True, inplace=True)
clean_crash_locations.drop('Unnamed: 0', axis=1, inplace=True)

In [23]:
latitude = []
longitude = []
for idx in range(clean_crash_locations.shape[0]):
    geo_to_coordinates = clean_crash_locations['geometry'][idx][7:-1].split(' ')
    latitude.append(geo_to_coordinates[1])
    longitude.append(geo_to_coordinates[0])
clean_crash_locations['longitude'] = longitude
clean_crash_locations['latitude'] = latitude
clean_crash_locations

geometry  \
0       POINT (37.6174943 55.7504461)   
1      POINT (120.9782618 14.5948914)   
2      POINT (-74.0060152 40.7127281)   
3       POINT (31.2357257 30.0443879)   
4     POINT (-46.6333824 -23.5506507)   
...                               ...   
2234    POINT (87.7945375 49.1713511)   
2235     POINT (138.730781 35.362799)   
2236     POINT (5.5524835 45.6657801)   
2237  POINT (-116.7651123 44.0374651)   
2238    POINT (74.6212807 30.9292303)   

                                                address  Number of Crashes  \
0         Москва, Центральный федеральный округ, Россия                 17   
1     Manila, Capital District, Metro Manila, Philip...                 14   
2             City of New York, New York, United States                 14   
3                                          القاهرة, مصر                 13   
4     São Paulo, Região Imediata de São Paulo, Regiã...                 13   
...                                                 ...                ...   
2234  хребет Южный Алтай, 禾木哈纳斯蒙古民族乡, 布尔津县, 阿勒泰地区, 新...                  1   
2235                             富士山, 小山町, 駿東郡, 静岡県, 日本                  1   
2236  Triel, Le Bouchage, La Tour-du-Pin, Isère, Auv...                  1   
2237               Payette County, Idaho, United States                  1   
2238  Rawalpindi Vaishno Dhaba, Sadar Bazaar, Firozp...                  1   

         longitude     latitude  
0       37.6174943   55.7504461  
1      120.9782618   14.5948914  
2      -74.0060152   40.7127281  
3       31.2357257   30.0443879  
4      -46.6333824  -23.5506507  
...            ...          ...  
2234    87.7945375   49.1713511  
2235    138.730781    35.362799  
2236     5.5524835   45.6657801  
2237  -116.7651123   44.0374651  
2238    74.6212807   30.9292303  

[2239 rows x 5 columns]

# Prensentation

## Stats

In [24]:
stat_cols = [
    'Aboard',
    'Aboard Passangers',
    'Aboard Crew',
    'Fatalities',
    'Fatalities Passangers',
    'Fatalities Crew',
    'Ground',
]
median_list = []
stats = pd.DataFrame()
for col in stat_cols:
    stats[col] = data[col].describe()
stats

Aboard  Aboard Passangers  Aboard Crew   Fatalities  \
count  4949.000000        4738.000000  4741.000000  4959.000000   
mean     31.088301          26.898691     4.479646    22.338173   
std      45.438282          44.010591     3.489021    35.026176   
min       0.000000           0.000000     0.000000     0.000000   
25%       7.000000           3.000000     2.000000     4.000000   
50%      16.000000          12.000000     4.000000    11.000000   
75%      35.000000          30.000000     6.000000    25.000000   
max     644.000000         614.000000    61.000000   583.000000   

       Fatalities Passangers  Fatalities Crew       Ground  
count            4725.000000      4726.000000  4926.000000  
mean               19.017566         3.579348     1.728177  
std                34.114849         3.170223    55.708966  
min                 0.000000         0.000000     0.000000  
25%                 1.000000         2.000000     0.000000  
50%                 8.000000         3.000000     0.000000  
75%                21.000000         5.000000     0.000000  
max               560.000000        46.000000  2750.000000

### Pancarköy Faciası

In [25]:
data.loc[data['Aboard Crew'] == 0]

Date   Time                          Location            datetime  \
55    04/06/1921    NaN             Point Cook, Australia 1921-04-06 12:00:00   
118   11/11/1926  08:00             Cape Bojador, Morocco 1926-11-11 08:00:00   
492   02/09/1938    NaN                 Guadalupe, Mexico 1938-02-09 12:00:00   
495   02/22/1938  04:45                  Pontoise, France 1938-02-22 04:45:00   
773   02/23/1945    NaN          Snezka mountains, Poland 1945-02-23 12:00:00   
3127  09/22/1981  12:00             Near Babaeski, Turkey 1981-09-22 12:00:00   
3359  03/27/1986    NaN  Bangui, Central African Republic 1986-03-27 12:00:00   

                                   Operator Flight #  \
55    Military - Royal Australian Air Force      NaN   
118                  Grands Express Aeriens      NaN   
492                                Mexicana      NaN   
495                      Deutsche Lufthansa      NaN   
773                  Military - German Army      NaN   
3127           Military - Turkish Air Force      NaN   
3359            Military - French Air Force      NaN   

                                Route            ACFT Type Registration cn/ln  \
55                                NaN          \t Avro 504        H3021   NaN   
118                 Casablanca -Dakar           Breguet 14       F-AFAX   198   
492                       Test flight  Lockheed 10 Electra       XA-BAS   NaN   
495   Berlin, Germany - Paris, France        Junkers JU.52       D-APAR  4040   
773                               NaN        Junkers 52/3m        4V+DR  6820   
3127                              NaN        Northrop F-5A          NaN   NaN   
3359                              NaN     Sepecat Jaguar A          NaN   NaN   

      Aboard  Aboard Passangers  Aboard Crew  Fatalities  \
55       2.0                0.0          0.0         2.0   
118      3.0                3.0          0.0         3.0   
492      2.0                0.0          0.0         2.0   
495      3.0                0.0          0.0         3.0   
773      8.0                8.0          0.0         8.0   
3127     0.0                0.0          0.0         0.0   
3359     0.0                0.0          0.0         0.0   

      Fatalities Passangers  Fatalities Crew  Ground  \
55                      0.0              0.0     0.0   
118                     3.0              0.0     0.0   
492                     0.0              0.0     0.0   
495                     0.0              0.0     0.0   
773                     8.0              0.0     0.0   
3127                    0.0              0.0    40.0   
3359                    0.0              0.0    35.0   

                                                Summary  
55    Shortly after taking off on a training flight,...  
118   While en route and cruising along the shore, t...  
492                    Crashed on a second test flight.  
495   The mail plane crashed in fog within a few mil...  
773   Crashed in the Snezka mountains during an ice ...  
3127  The fighter crashed into a village after the p...  
3359  The jet fighter crashed into a school shortly ...

In [26]:
pprint(data.iloc[3127]['Summary'])

'The fighter crashed into a village after the pilot ejected from the plane.'


#### Sources:

- [Source1](https://www.babaeskisozgazetesi.com/pancarkoy-sehitleri-38-yil-donumunde-kabirleri-basinda-anildi/)

- [Source2](https://www.alpullu.org/P/pancarkoy_sehitligi.html)

![alpullu](alpullu-pancarkoy_sehitligi-4.jpg)

![Pancarli](Pancarli.png)

### Tenerife

In [27]:
data.loc[data['Fatalities'] == 583]

Date   Time                  Location            datetime  \
2885  03/27/1977  17:07  Tenerife, Canary Islands 1977-03-27 17:07:00   

                              Operator   Flight #  \
2885  Pan American World Airways / KLM  1736/4805   

                                              Route  \
2885  Tenerife - Las Palmas / Tenerife - Las Palmas   

                                 ACFT Type   Registration  \
2885  Boeing B-747-121 / Boeing B-747-206B  N736PA/PH-BUF   

                     cn/ln  Aboard  Aboard Passangers  Aboard Crew  \
2885  19643/11 / 20400/157   644.0              614.0         30.0   

      Fatalities  Fatalities Passangers  Fatalities Crew  Ground  \
2885       583.0                  560.0             23.0     0.0   

                                                Summary  
2885  Both aircraft were diverted to Tenerife becaus...

In [28]:
pprint(data.iloc[2885]['Summary'])

('Both aircraft were diverted to Tenerife because of a bombing at Las Palmas '
 'Airport. After an extended delay,  both planes were instructed to back track '
 'up the runway. The KLM plane reached its takeoff point while the Pan Am '
 'plane was still on the runway. The Pan Am plane continued up the runway '
 'missing the taxiway turnout. There was heavy fog on the runway. The KLM '
 'plane began its takeoff roll without permission with the Pan Am plane still '
 'on the runway. The controller and Pan Am pilot each radioed a warning to the '
 'KLM plane, but were not heard because the simultaneous transmissions '
 'interfered with each other.The KLM plane hit the Pan Am plane just as it was '
 'taking off. Both planes burst into flames.  KLM 234 + 14 crew,  Pan Am 326 + '
 '9 crew killed. All aboard the KLM plane were killed. The KLM captain was '
 'their safety officer and for some months had  been training other pilots '
 'using a simulator, where getting takeoff permission was not 


[Youtube Video </br> ![thumbnail](thumbnail.jpg)](https://www.youtube.com/watch?v=2d9B9RN5quA&ab_channel=MentourPilot)</br>

![Tenerife](Tenerife.jpg)

### 9/11 Attacks

In [29]:
data.loc[data['Ground'] == 2750]

Date   Time                 Location            datetime  \
4328  09/11/2001  08:47  New York City, New York 2001-09-11 08:47:00   
4329  09/11/2001  09:03  New York City, New York 2001-09-11 09:03:00   

               Operator Flight #                 Route         ACFT Type  \
4328  American Airlines       11  Boston - Los Angeles  Boeing 767-223ER   
4329   United Air Lines      175  Boston - Los Angeles  Boeing B-767-222   

     Registration      cn/ln  Aboard  Aboard Passangers  Aboard Crew  \
4328       N334AA  22332/169    92.0               81.0         11.0   
4329       N612UA   21873/41    65.0               56.0          9.0   

      Fatalities  Fatalities Passangers  Fatalities Crew  Ground  \
4328        92.0                   81.0             11.0  2750.0   
4329        65.0                   56.0              9.0  2750.0   

                                                Summary  
4328  The aircraft was hijacked shortly after it lef...  
4329  The aircraft was hijacked shortly after it lef...

In [30]:
pprint(data.iloc[4328]['Summary'])
pprint(data.iloc[4329]['Summary'])

('The aircraft was hijacked shortly after it left Logan International Airport '
 'in Boston. The hijackers took control of the aircraft and deliberately '
 'crashed it into the north tower of the World Trade Center between the 94th '
 'and 99th floors at approximately 450 mph.  After 102 minutes, the building '
 'collapsed. It was one of four planes that were hijacked the same day.')
('The aircraft was hijacked shortly after it left Logan International Airport '
 'in Boston. The hijackers took control of the aircraft and deliberately '
 'crashed it into the south tower of the World Trade Center between the 78th '
 'and 84th floors at approximately 550 mph. After 56 minutes, the building '
 'collapsed. It was one of four planes that were hijacked the same day.')


[Wikipedia Page](https://en.wikipedia.org/wiki/September_11_attacks)

![9/11](911.webp)

### R-38 Airship

In [31]:
data.loc[data['Fatalities Crew'] == 46]

Date   Time               Location            datetime  \
60  08/24/1921  17:40  River Humber, England 1921-08-24 17:40:00   

                          Operator Flight # Route  \
60  Military - Royal Airship Works      NaN   NaN   

                             ACFT Type Registration cn/ln  Aboard  \
60  Royal Airship Works ZR-2 (airship)         R-38  R-38    46.0   

    Aboard Passangers  Aboard Crew  Fatalities  Fatalities Passangers  \
60                0.0         46.0        46.0                    0.0   

    Fatalities Crew  Ground                                            Summary  
60             46.0     1.0  Crashed due to structural failure followed by ...

In [32]:
pprint(data.iloc[60]['Summary'])

('Crashed due to structural failure followed by two explosions and a fire. '
 'Attributed to faulty design.')


[Wikipedia Page](https://en.wikipedia.org/wiki/R38-class_airship)

![Airship](Airship.jpg)
![R-38 Crash](r38.jpg)

## Correlations

In [33]:
px.imshow(data.corr(numeric_only=True), text_auto=True, aspect="auto", height=900, color_continuous_scale='purpor')

## Date Relations


In [34]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=data['datetime'], y=clean_data['Location'], mode='markers', visible=True))
fig.add_trace(go.Scatter(x=data['datetime'], y=clean_data['Operator'], mode='markers', visible=False))
fig.add_trace(go.Scatter(x=data['datetime'], y=clean_data['Route'], mode='markers', visible=False))
fig.add_trace(go.Scatter(x=data['datetime'], y=clean_data['ACFT Type'], mode='markers', visible=False))


fig.update_xaxes(showticklabels=False)
fig.update_traces(marker=dict(color='mediumpurple', size=3))
fig.update_layout(height=900, showlegend=False,
                margin=dict(l=20, r=10, t=20, b=0))
fig.update_layout(
    updatemenus=[
        dict(
            active=0,
            buttons=list([
                dict(label='Location',
                    method='update',
                    args=[{'visible': [True, False, False, False]}]),
                dict(label="Operator",
                    method='update',
                    args=[{'visible': [False, True, False, False]}]),
                dict(label='Route',
                    method='update',
                    args=[{'visible': [False, False, True, False]}]),
                dict(label='ACTF Type',
                    method='update',
                    args=[{'visible': [False, False, False, True]}]),
            ]),
        )
    ]
)

## Violin

In [35]:
px.violin(numeric_data, height=900).update_traces(marker=dict(color='mediumpurple'))

In [36]:
fig = go.Figure()
fig.add_trace(go.Violin(x=clean_data['Aboard'], visible=True))
fig.add_trace(go.Violin(x=clean_data['Fatalities'], visible=False))
fig.add_trace(go.Violin(x=clean_data['Ground'], visible=False))

fig.update_yaxes(showticklabels=False)
fig.update_traces(marker=dict(color='mediumpurple'))
fig.update_layout(height=900, showlegend=False,
                margin=dict(l=20, r=10, t=20, b=0))
fig.update_layout(
    updatemenus=[
        dict(
            active=0,
            buttons=list([
                dict(label='Location',
                    method='update',
                    args=[{'visible': [True, False, False]}]),
                dict(label='Operator',
                    method='update',
                    args=[{'visible': [False, True, False]}]),
                dict(label='Route',
                    method='update',
                    args=[{'visible': [False, False, True]}])
            ]),
        )
    ]
)

## Histogram

In [37]:
px.histogram(data['datetime'], height=900).update_traces(marker=dict(color='mediumpurple', line=dict(width=1)))

In [38]:
fig = go.Figure()
fig.add_trace(go.Histogram(x=clean_data['Location'], visible=True))
fig.add_trace(go.Histogram(x=clean_data['Operator'], visible=False))
fig.add_trace(go.Histogram(x=clean_data['Route'], visible=False))
fig.add_trace(go.Histogram(x=clean_data['ACFT Type'], visible=False))


fig.update_xaxes(showticklabels=False)
fig.update_traces(marker=dict(color='mediumpurple'))
fig.update_layout(height=900, showlegend=False,
                margin=dict(l=20, r=10, t=20, b=0))
fig.update_layout(
    updatemenus=[
        dict(
            active=0,
            buttons=list([
                dict(label='Location',
                    method='update',
                    args=[{'visible': [True, False, False, False]}]),
                dict(label='Operator',
                    method='update',
                    args=[{'visible': [False, True, False, False]}]),
                dict(label='Route',
                    method='update',
                    args=[{'visible': [False, False, True, False]}]),
                dict(label='ACTF Type',
                    method='update',
                    args=[{'visible': [False, False, False, True]}]),
            ]),
        )
    ]
)

### Aeroflot

[Wikipedia Page](https://en.wikipedia.org/wiki/Aeroflot)

![aeroflot](aeroflot.jpg)

In [39]:
data.loc[data['Operator'] == 'Aeroflot']['Fatalities'].max()

200.0

In [40]:
a = data['Fatalities'] == 200
b = data['Operator'] == 'Aeroflot'
c = a*b
data.loc[c]

Date   Time                        Location            datetime  \
3321  07/10/1985  23:46  Near Uchuduk, Uzbekistan, USSR 1985-07-10 23:46:00   

      Operator Flight #               Route          ACFT Type Registration  \
3321  Aeroflot     7425  Karshi - Leningrad  Tupolev TU-154B-2   CCCP-85311   

     cn/ln  Aboard  Aboard Passangers  Aboard Crew  Fatalities  \
3321   311   200.0              191.0          9.0       200.0   

      Fatalities Passangers  Fatalities Crew  Ground  \
3321                  191.0              9.0     0.0   

                                                Summary  
3321  The crew climbed to the cruising altitude of F...

In [41]:
pprint(list(data.loc[c]['Summary']))

['The crew climbed to the cruising altitude of FL380  at an airspeed of which '
 'is close to stall speed. During cruise flight vibrations started because of '
 'the low airspeed but were assumed by the crew to be  caused by engine '
 'surges. They reduced power to idle, causing the airspeed to drop. Trying to '
 'maintain altitude, the airplane eventually stalled, went into a flat spin '
 'and crashed.']


[Wikipedia Page](https://en.wikipedia.org/wiki/Aeroflot_Flight_5143)

![5143](5143.jpg)

### Douglas DC-3

[Wikipedia Page](https://en.wikipedia.org/wiki/Douglas_DC-3)

![dc3](douglas_dc3.webp)

In [42]:
data.loc[data['ACFT Type'] == 'Douglas DC-3']['Fatalities'].max()

39.0

In [43]:
k = data['Fatalities'] == 39
l = data['ACFT Type'] == 'Douglas DC-3'
m = k*l
data.loc[m]

Date   Time                  Location            datetime  \
1266  09/12/1951  12:30  Off Ialas Baeares, Spain 1951-09-12 12:30:00   

                    Operator Flight #             Route     ACFT Type  \
1266  Societe Alpes Provence      NaN  Perpignan - Oran  Douglas DC-3   

     Registration        cn/ln  Aboard  Aboard Passangers  Aboard Crew  \
1266       F-BEIZ  15985/32733    39.0               36.0          3.0   

      Fatalities  Fatalities Passangers  Fatalities Crew  Ground  \
1266        39.0                   36.0              3.0     0.0   

                                                Summary  
1266  Crashed into the Mediterranean due to structur...

In [44]:
pprint(list(data.loc[m]['Summary']))

['Crashed into the Mediterranean due to structural failure following loss of '
 'control in severe weather.']


[Accidents involving DC-3](https://en.wikipedia.org/wiki/List_of_accidents_and_incidents_involving_the_DC-3)

## Heatmap


In [45]:
crash_heatmap_data = clean_crash_locations[['latitude','longitude']].copy()
crash_heatmap_data['crash_weight'] = clean_crash_locations['Number of Crashes']/clean_crash_locations['Number of Crashes'].max()

In [50]:
wind_data = wind[['Latitude','Longitude']].copy()
wind_data['Speed'] = wind['Speed']/wind['Speed'].max()
wind_heatmap_data = wind_data.iloc[:3*WIND_INTERVAL] # 0-5000 ft.

In [52]:
# 'OpenStreetMap''Stamen Terrain' 'Stamen Toner' 'Stamen Watercolor' 'CartoDB positron' 'CartoDB dark_matter'

heat_map = folium.Map(tiles = 'CartoDB dark_matter',
                        control_scale = True,
                        location = [0, 0],
                        zoom_start = 3,
                        min_zoom = 2,
                        max_zoom = 6)

wind_heat = HeatMap(data=wind_heatmap_data,
                    name = 'Wind',
                    show = False,
                    radius = 35,
                    blur = 25,
                    min_opacity = 0,
                    gradient = {0.55: 'purple', 0.7: 'pink', 0.95: 'white'}).add_to(heat_map).overlay

crash_heat = HeatMap(data = crash_heatmap_data,
                    name = 'Crashes',
                    radius = 35,
                    min_opacity = 0.2,

                    gradient = {0.4: 'blue', 0.6: 'lime', 0.9: 'red'}).add_to(heat_map)
folium.LayerControl().add_to(heat_map)
heat_map